In [1]:
import os
import pandas as pd
import json
import datetime
from tqdm import tqdm
import pickle
from collections import Counter
import numpy as np
import requests

In [2]:
researcherPath = 'Files/Researchers'
errorPath = 'Files/ErrorResearchers'
researcherFiles = os.listdir(researcherPath)
errorFiles = os.listdir(errorPath)

df_researchers = pd.read_pickle("Files/Dataframes/researchers_allFrom2005.pkl")[['Year', 'Name', 'Institution', 'AuthorIndex', 'Title', 'SponsoringUnit', 'SessionIndex', 'SessionType', 'LowerCaseName']]

In [3]:
def readFile(file, path): #function to read file
    with open(path + file) as f:
        data = json.load(f)
    return data

In [4]:
def getName(data): #get namme from json
    name = data['File']['data'][0]['name'] #only save first name
        
    return name

In [5]:
def getAliases(data): #get aliases from json
    aliases = data['File']['data'][0]['aliases'] #only save first name
        
    return aliases

In [6]:
def findFirstName(name): #get first name from name
    firstName = name.replace('.', '').split()[0]
    
    return firstName

In [7]:
def getFirstName(searchName, API_name, aliasList): #assign searchName if first name is longer than 1 letter or no first names are longer than 1,assign API_name if first name is longer than 1 letter, assign first alias with firs name longer than 1 letter
    firstName = findFirstName(searchName)
    if len(firstName) <= 1: #if first name consists of 1 or less letters
        firstName_API = findFirstName(API_name)
        if len(firstName_API) <= 1 and aliasList: #if first name consists of 1 or less letters
            for i in aliasList:
                firstName_alias = findFirstName(i)
                if len(firstName_alias) > 1: #if alias first name is longer than 1 letter, save that name
                    assignedFirstName = firstName_alias
                    break
                else:
                    assignedFirstName = firstName
        else:
            assignedFirstName = firstName_API
    else: 
        assignedFirstName = firstName
        
    return assignedFirstName

In [8]:
def getPublicationData(data): #get dict with number of publications for each year
    publishCount = {}
    paper_data = data['papers']
    n_papers = len(paper_data)
    for p in range(0, n_papers):
        year = paper_data[p]['year']
        if year in publishCount:
            publishCount[year]+= 1 #add 1 to count
        else:
            publishCount[year] = 1 #create year, as set count as 1
                
    return publishCount

In [9]:
def getAPI_field(data): #get field from API
    fields = []
    noneCount = 0
    paper_data = data['papers']
    n_papers = len(paper_data)
    for p in range(0, n_papers):
        field = paper_data[p]['fieldsOfStudy']
        if field:
            fields += paper_data[p]['fieldsOfStudy']
        else:
            noneCount += 1
    if fields:
        assignedField = Counter(fields).most_common(1)[0][0] #assign most occurring field
        fieldCount = Counter(fields).most_common(1)[0][1]
    else:
        assignedField = 'Unknown'
        fieldCount = noneCount
        #fieldCount = 'Unknown'
        
    return assignedField, fieldCount

In [10]:
def getFieldOfStudy_both(data): #get both external and model 
    #fields_dict = {}
    externalFields = []
    modelFields = []
    paper_data = data['papers']
    n_papers = len(paper_data)
    for p in range(0, n_papers):
        fields = paper_data[p]['s2FieldsOfStudy']
        for f in fields:
            if f['source'] == 'external':
                externalField = f['category']
                externalFields.append(externalField)
            elif f['source'] == 's2-fos-model':
                modelField = f['category']
                modelFields.append(modelField)
            else:
                print("No field")
    if externalFields: 
        assignedExternalField = Counter(externalFields).most_common(1)[0][0] #assign most occurring field
        externalFieldCount = Counter(externalFields).most_common(1)[0][1] #number of times most occuring field is assigned
    else:
        assignedExternalField = "Unknown"
        externalFieldCount = 0
        
    if modelFields:
        assignedModelField = Counter(modelFields).most_common(1)[0][0] #assign most occurring field
        modelCount = Counter(modelFields).most_common(1)[0][1] #number of times most occuring field is assigned
    else:
        assignedModelField = 'Unknown'
        modelCount = 0
    
    return assignedExternalField, assignedModelField, externalFieldCount, modelCount

In [11]:
def getAuthorInfo(files, path): #get info about authors
    error = {}
    researcher_dict = {}
    publicationData = {}
    for file in tqdm(files):
        if file != '.DS_Store':
            data = readFile(file, path)
            for key in data.keys():
                researcher_data = data[key]
                searchName = researcher_data['SearchName'] #name searched on
                if researcher_data['File']['data'][0]['papers']: #if any data on papers
                    API_name = getName(researcher_data) #name returned
                    aliases = getAliases(researcher_data) #get aliases
                    firstName = getFirstName(searchName, API_name, aliases)
                    dataCount = data[key]['File']['total'] #authorResults
                    authorData = data[key]['File']['data'][0] #only data from first author
                    publicationData[key] = getPublicationData(authorData)
                    if len(publicationData[key]) == 1 and publicationData[key].get(None): #if there's only 1 year,a nd the year is None
                        error[key] = {'SearchName': searchName}
                    else:
                        maxPaperCount = sum(publicationData[key].values())
                        API_field, API_fieldCount = getAPI_field(authorData) #get assigned field(can be based on external soruces or API)
                        field_external, field_model, fieldCount_external, fieldCount_model = getFieldOfStudy_both(authorData)
                        firstYear = min(list(filter(None,publicationData[key].keys())))
                        researcher_dict[key] = {'SearchName': searchName, 'API_Name': API_name, 'FirstName': firstName, 'AuthorCount': dataCount, 'MaxPaperCount': maxPaperCount, 'API_Field': API_field, 'API_FieldCount': API_fieldCount, 'ExternalField': field_external, 'ModelField': field_model, 'ExternalFieldCount': fieldCount_external, 'ModelFieldCount': fieldCount_model, 'FirstPaperYear': firstYear}
                else:
                    error[key] = {'SearchName': searchName}
    
    return researcher_dict, error, publicationData

In [12]:
def getErrorResearchers(files, path): #get searchName and ID of researchers that could not be found
    error = {}
    for file in tqdm(files):
        if file != '.DS_Store':
            data = readFile(file, path)
            for key in data.keys():
                searchName = data[key]
                error[key] = {'SearchName': searchName}
    return error

In [13]:
def getCumulativePaperCount(confYear, ID, publicationDict):
    publishCount = 0
    publications = publicationDict[str(ID)]
    for key in publications:
        if key != None:
            if key < confYear :
                publishCount += publications[key]
            
    return publishCount

In [14]:
def getFirstName_errorResearchers(df, searchNameCol):
    firstName_dict = {}
    for i in df.index:
        ID = df.iloc[i]['ID']
        name = df[searchNameCol].iloc[i].split()
        firstName = name[0]
        firstName_dict[ID] = firstName
    
    return firstName_dict

#### Add additional information

In [15]:
researcherDict, errorDict, publicationData = getAuthorInfo(researcherFiles, researcherPath + "/") #dict with researcher info

100%|█████████████████████████████████████████| 187/187 [01:00<00:00,  3.07it/s]


In [16]:
#create df from researcherInfo
researcher_df = pd.DataFrame.from_dict(researcherDict, orient = 'index').reset_index().rename(columns = {'index': 'ID'})

In [17]:
#add information about researchers from API to df with researchers
researchers = pd.merge(researcher_df, df_researchers, how = 'inner', left_on = 'SearchName', right_on = 'LowerCaseName')#add information to df

In [18]:
#add seniority
researchers['Seniority'] = researchers.Year - researchers.FirstPaperYear 

In [19]:
#apply function to calculate cumulative paper count for current conference year
researchers['CumulativePaperCount'] = researchers.apply(lambda x: getCumulativePaperCount(x.Year, x.ID, publicationData), axis = 1)

In [20]:
#add productivity (cumulative papercount / years in the field)
researchers['Productivity'] = researchers.CumulativePaperCount/researchers.Seniority

### Researchers not found

In [21]:
errorResearchers = getErrorResearchers(errorFiles, errorPath + "/")

100%|███████████████████████████████████████| 187/187 [00:00<00:00, 4655.80it/s]


In [22]:
#create df with researchers not found or with no data from the API
errorResearchers_df = pd.DataFrame.from_dict(errorResearchers, orient = 'index').reset_index().rename(columns = {'index': 'ID'})

### Try API again

In [23]:
#check response
def checkResponse(response):
    if 'message' in response.keys():
        status = 'error'
    elif not response['data']:
        status = 'error'
    else:
        status = 'correct'
    
    return status

In [24]:
def saveAuthor(dict_, url, APIkey, timeoutTime, researcherPath, errorPath):
    researcherDict = {}
    errorDict = {} #dict for reseachers with error
    for key in tqdm(dict_):
        name = dict_[key]
        parameters = {
            "query": name,
            "fields": "name,paperCount,citationCount,hIndex,aliases,papers.title,papers.fieldsOfStudy,papers.s2FieldsOfStudy,papers.referenceCount,papers.year,papers.citationCount,papers.influentialCitationCount,papers.publicationDate"
            }
        try:
            response = requests.get(url, params = parameters, headers = APIkey, timeout = timeoutTime).json()
            
        except:
            errorDict[str(key)] = name
            print(key, name)
            continue
            
        if response: 
            status = checkResponse(response)
            if status == 'error': #check if response were found
                errorDict[str(key)] = name
                print(key, name)
            else:
                researcherDict[str(key)] = {'SearchName': name, 'File': response} #key is the ID
            
        if key%1000 == 0 and key != 0 or key == max(dict_.keys()): #save for each 1000 and the last names
            with open(researcherPath + str(key) + '.txt', "w") as f:
                json.dump(researcherDict, f) #save
                researcherDict = {}
            with open(errorPath + 'error' + str(key) + '.txt', 'w') as f:
                json.dump(errorDict, f) #save
                errorDict = {}

In [25]:
url = "https://api.semanticscholar.org/graph/v1/author/search?&limit=1"
APIkey = {'x-api-key': 'tRss0MQnxJaaE0KmrqBUr7gGK2Y7Bm8C8UdCCLzP'}

In [26]:
#create new ID and new db with error researchers and new ID
ID = np.arange(0,len(errorResearchers_df.SearchName.unique())) #id of 0 to length of unique names
errorResearcher_db = dict(zip(ID, errorResearchers_df.SearchName.unique())) #dict with error researcher name(lowercase) and ID

In [27]:
saveAuthor(errorResearcher_db, url, APIkey, 12, 'Files/Researchers_NewTry/', 'Files/ErrorResearchers_NewTry/')

  0%|                                       | 1/12326 [00:00<2:41:00,  1.28it/s]

0 cea/inac/sp2m


  0%|                                       | 2/12326 [00:01<2:16:56,  1.50it/s]

1 swathy natarajan


  0%|                                       | 3/12326 [00:01<2:08:39,  1.60it/s]

...

12323 kolmogorov group


100%|██████████████████████████████████▉| 12325/12326 [4:42:51<00:00,  1.88it/s]

12324 niall b devlin


100%|███████████████████████████████████| 12326/12326 [4:42:52<00:00,  1.38s/it]

12325 maria-teresa handschuh


In [28]:
#new files
researcherPath_newTry = 'Files/Researchers_NewTry'
errorPath_newTry = 'Files/ErrorResearchers_NewTry'
researcherFiles_newTry = os.listdir(researcherPath_newTry)
errorFiles_newTry = os.listdir(errorPath_newTry)

In [29]:
researcherDict_newTry, errorDict_newTry, publicationData_newTry = getAuthorInfo(researcherFiles_newTry, researcherPath_newTry + "/") #dict with researcher info

100%|███████████████████████████████████████████| 15/15 [00:00<00:00, 57.60it/s]


In [30]:
#create df from researcherInfo
researcher_df_newTry = pd.DataFrame.from_dict(researcherDict_newTry, orient = 'index').reset_index().rename(columns = {'index': 'ID'})

In [31]:
#add information about researchers from API to df with researchers
researchers_newTry = pd.merge(researcher_df_newTry, df_researchers, how = 'inner', left_on = 'SearchName', right_on = 'LowerCaseName')#add information to df

#### Add additional information with new try

In [32]:
#add seniority
researchers_newTry['Seniority'] = researchers_newTry.Year - researchers_newTry.FirstPaperYear 

In [33]:
#apply function to calculate cumulative paper count for current conference year
researchers_newTry['CumulativePaperCount'] = researchers_newTry.apply(lambda x: getCumulativePaperCount(x.Year, x.ID, publicationData_newTry), axis = 1)

In [34]:
#add productivity (cumulative papercount / years in the field)
researchers_newTry['Productivity'] = researchers_newTry.CumulativePaperCount/researchers_newTry.Seniority

### Join datasets with the found researchers

In [35]:
#join researchers and researchers_newTry
researchers_joined = pd.concat([researchers, researchers_newTry])

In [36]:
#select only first names longer than one letter
researchers_realNames = researchers_joined[researchers_joined.FirstName.str.len() > 1]

In [37]:
#save researchers with all current columns
researchers_realNames.to_pickle("Files/DataFrames/apiResearchers_allColumns.pkl") 

In [38]:
#researchers with name columns deleted
researchers_nameColDel = researchers_realNames.drop(['API_Name', 'LowerCaseName'], axis = 1)

In [39]:
#save researchers again with the current columns(with some of the names columns deleted)
researchers_nameColDel.to_pickle("Files/DataFrames/apiResearchers_fewNameCol.pkl") 

### Researchers still not found after second try

In [40]:
errorResearchers_newTry = getErrorResearchers(errorFiles_newTry, errorPath_newTry + "/")

100%|█████████████████████████████████████████| 15/15 [00:00<00:00, 1747.24it/s]


In [41]:
#create df with researchers not found or with no data from the API
errorResearchers_df_newTry = pd.DataFrame.from_dict(errorResearchers_newTry, orient = 'index').reset_index().rename(columns = {'index': 'ID'})

### Researchers with no data

In [42]:
#researchers with no data from API (first and second try)
researchers_noData = pd.DataFrame.from_dict(errorDict, orient = 'index').reset_index().rename(columns = {'index': 'ID'})
researchers_noData_newTry = pd.DataFrame.from_dict(errorDict_newTry, orient = 'index').reset_index().rename(columns = {'index': 'ID'})

In [43]:
researcher_noData_joined = pd.concat([researchers_noData, researchers_noData_newTry])

### Missing researchers

Missing researchers are those that the API is still not able to find or get data on.

In [44]:
#all researchers missing(regardless of the reason)
researchers_missing_df = pd.concat([errorResearchers_df_newTry, researcher_noData_joined]).drop_duplicates(subset = 'SearchName')

In [45]:
#create new unique ID
researchers_missing_df['ID'] = researchers_missing_df.groupby(['SearchName']).ngroup()

In [46]:
#add already known information to df for researchers not found
researchers_missing = pd.merge(researchers_missing_df, df_researchers,  how = 'inner',  left_on = 'SearchName', right_on = 'LowerCaseName')  

In [47]:
#crete dict with first name
firstNameDict_missingResearchers = getFirstName_errorResearchers(researchers_missing, 'SearchName')
#make function such that it uses the ID as index

#make firstNameDict to df
firstName_missingResearchers_df = pd.DataFrame.from_dict(firstNameDict_missingResearchers, orient = 'index').reset_index().rename(columns = {'index': 'ID', 0: 'FirstName'})

In [48]:
#add first name to df
apiResearchers_notFound = pd.merge(researchers_missing, firstName_missingResearchers_df,  on = ['ID'])

In [49]:
print("Number of researchers with no data/not found:", len(apiResearchers_notFound.SearchName.unique()))
print("Number of researchers found:", len(researchers_realNames.SearchName.unique()))
print("Number of researchers removed due to not knowing their first name:", len(researchers_joined[researchers_joined.FirstName.str.len() <= 1]))

Number of researchers with no data/not found: 13010
Number of researchers found: 168422
Number of researchers removed due to not knowing their first name: 10062


In [50]:
#save researchers not found
apiResearchers_notFound.to_pickle("Files/DataFrames/researcherNotFound.pkl") 